In [8]:
import xarray as xr
import dask as da
import pandas as pd
import numpy as np
import requests
import cartopy
import time,os
import geoviews as gv
#import rasterio as rs
import rioxarray
import shapefile
import matplotlib.pyplot as plt
import cartopy.feature as cfeature
from cartopy.feature import ShapelyFeature
import cartopy.io.shapereader as shpreader
from shapely import geometry
import datashader
import hvplot.xarray
import cmocean.cm as cmo
import xcmocean
import xesmf as xe
from rioxarray import merge
import geopandas
from shapely.geometry import box

In [9]:
from dask.distributed import Client
import dask.array as da
client = Client()
client

/home/hunter/miniconda3/envs/XROMS/lib/python3.8/site-packages/distributed/node.py:183: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 34436 instead
  warnings.warn(


<Client: 'tcp://127.0.0.1:35083' processes=6 threads=36, memory=376.39 GiB>

In [10]:
file=r'/home/hunter/roms/NOPP/grids/michael_grd3.nc'
proj = cartopy.crs.Mercator(central_longitude=-98)
pc = cartopy.crs.PlateCarree()
grd1 = xr.open_dataset(file,chunks={'eta_rho':900,'xi_rho':600}) 
grd1=grd1.set_coords(('lat_rho','lon_rho'))

grdH=grd1.h.load()
grdH = grdH.rename({"lon_rho": "lon", "lat_rho": "lat"})

glon=np.concatenate((grd1.lon_rho[0,:].values,grd1.lon_rho[:,-1].values,np.flip(grd1.lon_rho[-1,:].values),np.flip(grd1.lon_rho[:,0].values)))  
glat=np.concatenate((grd1.lat_rho[0,:].values,grd1.lat_rho[:,-1].values,np.flip(grd1.lat_rho[-1,:].values),np.flip(grd1.lat_rho[:,0].values)))  

llbounds=d = np.column_stack((glon,glat))

geodf = geopandas.GeoDataFrame(
    geometry=[
        box(glon.min(),glat.min(), glon.max(), glat.max())
    ],
    crs="EPSG:4326"
)



In [11]:
geodf

geometry
0  POLYGON ((-85.38848 29.75046, -85.38848 29.777...

In [17]:
%%time
infile=r'/home/hunter/roms/NOPP/data/FPH_NOPP_Fusion/FPH_NOPP_Fusion_SUBSET2.tif'
#

img=rioxarray.open_rasterio(infile,masked=True)
img=img.squeeze()
img = img.rio.reproject("EPSG:4326")
#img = img.rio.clip(geodf.geometry.values, geodf.crs, drop=False, invert=True,from_disk=True)

CPU times: user 3.33 s, sys: 381 ms, total: 3.71 s
Wall time: 3.33 s


In [13]:
img=img.where(img.data<50)
#np.unique(img.data)

In [16]:
img

<xarray.DataArray (y: 9194, x: 11028)>
array([[nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       ...,
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan]], dtype=float32)
Coordinates:
  * x            (x) float64 -85.46 -85.46 -85.46 ... -85.35 -85.35 -85.35
  * y            (y) float64 29.81 29.81 29.81 29.81 ... 29.72 29.72 29.72 29.72
    band         int64 1
    spatial_ref  int64 0
Attributes:
    AREA_OR_POINT:  Area
    scale_factor:   1.0
    add_offset:     0.0
    _FillValue:     3.402823466e+38

In [14]:
%%time
varint = xr.Dataset({"lat": (["eta_rho","xi_rho"], grd1.lat_rho.values), "lon": (["eta_rho","xi_rho"], grd1.lon_rho.values)})
varint=varint.set_coords(('lat','lon'))

#mnlon=np.min(lon)
#mxlon=np.max(lon)
#mnlat=np.min(lat)
#mxlat=np.max(lat)
#img2=img.sel(lat=slice(mxlat,mnlat),lon=slice(mnlon,mxlon))
#    print(img2.sizes)
#    img2 = img2.rename({"x": "lon", "y": "lat"})
#regridder = xe.Regridder(img3, varint, "bilinear", locstream_out=False, filename='sanibel_weights', reuse_weights=True)
#regridder = xe.Regridder(img3, varint, "nearest_s2d", locstream_out=False, filename='sanibel_weights')
regridder = xe.Regridder(img, varint, "nearest_s2d", locstream_out=False)
 #  print(lon.shape)
y=regridder(img, keep_attrs=True)

CPU times: user 7min 52s, sys: 9.91 s, total: 8min 2s
Wall time: 7min 22s


In [22]:
y=regridder(img, keep_attrs=True)

In [23]:
y

<xarray.DataArray (eta_rho: 650, xi_rho: 550)>
array([[21., 21., 21., ..., 21., 21., 21.],
       [21., 21., 21., ..., 21., 21., 21.],
       [21., 21., 21., ..., 21., 21., 21.],
       ...,
       [21., 21., 21., ..., 21., 21., 21.],
       [21., 21., 21., ..., 21., 21., 21.],
       [21., 21., 21., ..., 21., 21., 21.]], dtype=float32)
Coordinates:
    band         int64 1
    spatial_ref  int64 0
    lon          (eta_rho, xi_rho) float64 -85.41 -85.41 -85.41 ... -85.4 -85.4
    lat          (eta_rho, xi_rho) float64 29.75 29.75 29.75 ... 29.78 29.78
Dimensions without coordinates: eta_rho, xi_rho
Attributes:
    AREA_OR_POINT:  Area
    scale_factor:   1.0
    add_offset:     0.0
    _FillValue:     3.402823466e+38
    regrid_method:  nearest_s2d

In [15]:
#img.hvplot.quadmesh(x='x', y='y',crs=pc,rasterize=True,cmap='seismic',subplots=True,shared_axes=True)
y.hvplot.quadmesh(x='lon', y='lat',crs=pc, rasterize=True,clim=(0,29),cmap='Category20',subplots=True,shared_axes=True)+img.hvplot.image(x='x', y='y',crs=pc,rasterize=True,clim=(0,29),cmap='Category20',subplots=True,shared_axes=True)
#da = da.rio.reproject("EPSG:4326")

:Layout
   .DynamicMap.I  :DynamicMap   []
      :Image   [lon,lat]   (value)
   .DynamicMap.II :DynamicMap   []
      :Image   [x,y]   (value)

:DynamicMap   []
   :Image   [lon,lat]   (h)

In [20]:
from osgeo import gdal
import numpy as np
import pandas as pd
import subprocess
infile=r'/home/hunter/roms/NOPP/vegetation/FPH_NOPP_Fusion/FPH_NOPP_Fusion.tif'

ModuleNotFoundError: No module named 'osgeo'

'/home/hunter/roms/NOPP/vegetation/FPH_NOPP_Fusion/FPH_NOPP_Fusion.tif'